### Load Data

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
!pip install pandas pyarrow datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.7 MB/s eta 0:00:00


In [62]:
from drive.MyDrive.Berkeley.MIDS.DATASCI_266.project.scripts.exact_match import ExactMatch

In [63]:
data_file_path = "/content/drive/MyDrive/Berkeley/MIDS/DATASCI_266/project/data/nq_open/validation-00000-of-00001.parquet"

In [64]:
import pandas as pd

# Load the Parquet file
df = pd.read_parquet(data_file_path, engine='pyarrow')

In [65]:
df.head()

question  \
0      when was the last time anyone was on the moon   
1    who wrote he ain't heavy he's my brother lyrics   
2  how many seasons of the bastard executioner ar...   
3            when did the eagles win last super bowl   
4        who won last year's ncaa women's basketball   

                                  answer  
0  [14 December 1972 UTC, December 1972]  
1             [Bobby Scott, Bob Russell]  
2                      [one, one season]  
3                                 [2017]  
4                       [South Carolina]

### Load LLM

In [7]:
!CMAKE_ARGS="-DLLAMA_CUBLAS=on" pip install llama-cpp-python

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.9/36.9 MB 26.2 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 7.0 MB/s eta 0:00:00
  Created wheel for llama-cpp-python: filename=llama_cpp_python-0.2.57-cp310-cp310-manylinux_2_35_x86_64.whl size=26393815 sha256=b22397c942a6b59425372fd7f842151b36534921ff3ff12f2061a2aa4bc48092
  Stored in directory: /root/.cache/pip/wheels/7e/c0/00/e98d6e198f941c623da37b3f674354cbdccfcfb2cb9cf1133d
Successfully built llama-cpp-python


In [8]:
%pip install llama-index-llms-llama-cpp

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.4/15.4 MB 45.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 13.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 108.0/108.0 kB 16.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 262.4/262.4 kB 27.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 31.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.8/77.8 kB 10.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 6.5 MB/s eta 0:00:00


In [11]:
from llama_index.llms.llama_cpp import LlamaCPP

# model_url = "https://huggingface.co/TheBloke/Llama-2-13B-chat-GGML/resolve/main/llama-2-13b-chat.ggmlv3.q4_0.bin"
model_url = "https://huggingface.co/TheBloke/Llama-2-13B-chat-GGUF/resolve/main/llama-2-13b-chat.Q4_0.gguf"

n_gpu_layers = 40 # Change this value based on your model and your GPU VRAM pool.
llm = LlamaCPP(
    # You can pass in the URL to a GGML model to download it automatically
    model_url=model_url,
    # optionally, you can set the path to a pre-downloaded model instead of model_url
    model_path=None,
    temperature=0.1,
    max_new_tokens=256,
    # llama2 has a context window of 4096 tokens, but we set it lower to allow for some wiggle room
    context_window=3900,
    # kwargs to pass to __call__()
    generate_kwargs={},
    # kwargs to pass to __init__()
    # set to at least 1 to use GPU
    model_kwargs={"n_gpu_layers": n_gpu_layers},
    #verbose=True,
)

llama_model_loader: loaded meta data with 19 key-value pairs and 363 tensors from /tmp/llama_index/models/llama-2-13b-chat.Q4_0.gguf (version GGUF V2)
llama_model_loader: Dumping metadata keys/values. Note: KV overrides do not apply in this output.
llama_model_loader: - kv   0:                       general.architecture str              = llama
llama_model_loader: - kv   1:                               general.name str              = LLaMA v2
llama_model_loader: - kv   2:                       llama.context_length u32              = 4096
llama_model_loader: - kv   3:                     llama.embedding_length u32              = 5120
llama_model_loader: - kv   4:                          llama.block_count u32              = 40
llama_model_loader: - kv   5:                  llama.feed_forward_length u32              = 13824
llama_model_loader: - kv   6:                 llama.rope.dimension_count u32              = 128
llama_model_loader: - kv   7:                 llama.attention.head_co

### Inference

In [12]:
!pip install tqdm

In [59]:
PROMPT_TEMPLATE = """
[INST] <<SYS>>
This is a Open Domain Question Answering Task. You are given a question and you need to generate
the short answer based on the question. Below are a few examples:
Question: where did they film hot tub time machine
Answer: Fernie Alpine Resort
Question: who has the right of way in international waters
Answer: Neither vessel
Question: who does annie work for attack on titan
Answer: Marley
Question: when was the immigration reform and control act passed
Answer: November 6, 1986
[ENDSYS]
<</SYS>>
Question: {prompt}[/INST]
"""

In [60]:
def generate_answer(question, index):
    # Format the PROMPT_TEMPLATE with the actual question
    formatted_prompt = PROMPT_TEMPLATE.format(prompt=question)
    try:
        response = llm.complete(formatted_prompt)
        answer = response.text
        print(f"Index: {index}, Question: '{question}', Generated Answer: '{answer}'")
        return answer
    except Exception as e:
        print(f"Error generating answer for question '{question}' at index {index}: {e}")
        return None

In [61]:
eval_file_path = "/content/drive/MyDrive/Berkeley/MIDS/DATASCI_266/project/eval/nq_open_llama2.csv"

In [73]:
try:
    # Try to load the DataFrame from the CSV file
    df_eval = pd.read_csv(eval_file_path)
    print("Data loaded from file.")
except FileNotFoundError:
    # If the file doesn't exist, copy df into df_eval
    df_eval = df.copy()
    if 'predictions' not in df_eval.columns:
      df_eval['predictions'] = pd.NA  # or use None or np.nan, depending on your preference
    print("File not found. Copied df into df_eval.")

File not found. Copied df into df_eval.


In [74]:
from tqdm import tqdm

# Initialize a counter for tracking when to save the DataFrame
save_counter = 0

for index, row in tqdm(df_eval.iterrows(), total=df_eval.shape[0], desc="Generating Answers"):
    # Check if 'predictions' is empty for the current row
    if pd.isna(row['predictions']) or row['predictions'] == '':
        # Generate the answer only if 'predictions' is empty
        df_eval.at[index, 'predictions'] = generate_answer(row['question'], index)

        # Increment the save counter
        save_counter += 1

        # Save the DataFrame back to the file every 10 rows
        if save_counter % 10 == 0:
            df_eval.to_csv(eval_file_path, index=False)
            print(f"Progress saved at index {index}")

# Save any remaining progress at the end of the loop
if save_counter % 10 != 0:
    df_eval.to_csv(eval_file_path, index=False)
    print("Final progress saved.")

Generating Answers:   0%|          | 0/3610 [00:00<?, ?it/s]Llama.generate: prefix-match hit

llama_print_timings:        load time =     988.94 ms
llama_print_timings:      sample time =      19.30 ms /    28 runs   (    0.69 ms per token,  1450.55 tokens per second)
llama_print_timings: prompt eval time =   14554.27 ms /    32 tokens (  454.82 ms per token,     2.20 tokens per second)
llama_print_timings:        eval time =    1515.34 ms /    27 runs   (   56.12 ms per token,    17.82 tokens per second)
llama_print_timings:       total time =    2163.56 ms /    59 tokens
Generating Answers:   0%|          | 1/3610 [00:03<3:22:36,  3.37s/it]Llama.generate: prefix-match hit


Index: 0, Question: 'when was the last time anyone was on the moon', Generated Answer: 'Answer: The last time anyone was on the moon was during the Apollo 17 mission in December 1972.'



llama_print_timings:        load time =     988.94 ms
llama_print_timings:      sample time =       5.58 ms /     9 runs   (    0.62 ms per token,  1613.19 tokens per second)
llama_print_timings: prompt eval time =     504.71 ms /    19 tokens (   26.56 ms per token,    37.65 tokens per second)
llama_print_timings:        eval time =     425.56 ms /     8 runs   (   53.19 ms per token,    18.80 tokens per second)
llama_print_timings:       total time =    1026.67 ms /    27 tokens
Generating Answers:   0%|          | 2/3610 [00:04<2:00:11,  2.00s/it]Llama.generate: prefix-match hit


Index: 1, Question: 'who wrote he ain't heavy he's my brother lyrics', Generated Answer: 'Answer: Bobby Scott and Bob Russell.'



llama_print_timings:        load time =     988.94 ms
llama_print_timings:      sample time =       9.81 ms /    17 runs   (    0.58 ms per token,  1732.75 tokens per second)
llama_print_timings: prompt eval time =     406.11 ms /    16 tokens (   25.38 ms per token,    39.40 tokens per second)
llama_print_timings:        eval time =     829.65 ms /    16 runs   (   51.85 ms per token,    19.29 tokens per second)
llama_print_timings:       total time =    1298.86 ms /    32 tokens
Generating Answers:   0%|          | 3/3610 [00:06<1:49:35,  1.82s/it]Llama.generate: prefix-match hit


...


llama_print_timings:        load time =     988.94 ms
llama_print_timings:      sample time =      11.85 ms /    18 runs   (    0.66 ms per token,  1518.99 tokens per second)
llama_print_timings: prompt eval time =     530.32 ms /    16 tokens (   33.15 ms per token,    30.17 tokens per second)
llama_print_timings:        eval time =     960.39 ms /    17 runs   (   56.49 ms per token,    17.70 tokens per second)
llama_print_timings:       total time =    1606.12 ms /    33 tokens
Generating Answers: 100%|█████████▉| 3609/3610 [2:32:28<00:01,  1.91s/it]Llama.generate: prefix-match hit


Index: 3608, Question: 'what domain has more individuals than all other domains combined do', Generated Answer: 'Answer: The domain of bacteria has more individuals than all other domains combined.'



llama_print_timings:        load time =     988.94 ms
llama_print_timings:      sample time =     105.12 ms /   155 runs   (    0.68 ms per token,  1474.52 tokens per second)
llama_print_timings: prompt eval time =     458.49 ms /    13 tokens (   35.27 ms per token,    28.35 tokens per second)
llama_print_timings:        eval time =    8529.06 ms /   154 runs   (   55.38 ms per token,    18.06 tokens per second)
llama_print_timings:       total time =   10062.93 ms /   167 tokens
Generating Answers: 100%|██████████| 3610/3610 [2:32:38<00:00,  4.43s/it]

Index: 3609, Question: 'what is the meaning of the name comanche', Generated Answer: 'Answer: The Comanche people were a Native American tribe that lived in the Great Plains of North America, specifically in present-day Texas, Oklahoma, Kansas, and New Mexico. The name "Comanche" is derived from the Ute word "komanche," which means "enemy." The Comanche were known for their fierce warrior culture, their skill in hunting and horse riding, and their intricate beadwork and quillwork. They were also known for their nomadic lifestyle, often moving their campsites in search of food and resources. Today, there are still Comanche communities and descendants of the Comanche people living in the United States and Mexico, preserving their cultural heritage and traditions.'
Progress saved at index 3609


Generating Answers: 100%|██████████| 3610/3610 [2:32:39<00:00,  2.54s/it]


In [77]:
df_eval.head()

question  \
0      when was the last time anyone was on the moon   
1    who wrote he ain't heavy he's my brother lyrics   
2  how many seasons of the bastard executioner ar...   
3            when did the eagles win last super bowl   
4        who won last year's ncaa women's basketball   

                                  answer  \
0  [14 December 1972 UTC, December 1972]   
1             [Bobby Scott, Bob Russell]   
2                      [one, one season]   
3                                 [2017]   
4                       [South Carolina]   

                                         predictions  
0  Answer: The last time anyone was on the moon w...  
1               Answer: Bobby Scott and Bob Russell.  
2  Answer: There is only one season of "The Basta...  
3  Answer: The Eagles won their last Super Bowl i...  
4                          Answer: Baylor Lady Bears

## Save evaluation data

In [40]:
df_eval.to_csv(eval_file_path, index=False)

## Evaluation metrics

In [41]:
!pip install pandas pyarrow datasets

In [42]:
import pandas as pd

In [43]:
eval_file_path = "/content/drive/MyDrive/Berkeley/MIDS/DATASCI_266/project/eval/nq_open_llama2.csv"

In [44]:
df = pd.read_csv(eval_file_path)

In [45]:
df.head()

question  \
0      when was the last time anyone was on the moon   
1    who wrote he ain't heavy he's my brother lyrics   
2  how many seasons of the bastard executioner ar...   
3            when did the eagles win last super bowl   
4        who won last year's ncaa women's basketball   

                                     answer  \
0  ['14 December 1972 UTC' 'December 1972']   
1             ['Bobby Scott' 'Bob Russell']   
2                      ['one' 'one season']   
3                                  ['2017']   
4                        ['South Carolina']   

                                         predictions  
0  Answer: The last time anyone was on the moon w...  
1               Answer: Bobby Scott and Bob Russell.  
2  Answer: There is only one season of "The Basta...  
3  Answer: The Eagles won their last Super Bowl i...  
4                          Answer: Baylor Lady Bears

In [46]:
print(df.iloc[1]['answer'])

['Bobby Scott' 'Bob Russell']


In [47]:
import ast
import string
import re
from drive.MyDrive.Berkeley.MIDS.DATASCI_266.project.scripts.exact_match import normalize_answer

def string_to_list(string):
    try:
        # Convert the string to a list
        matches = re.findall(r"'(.*?)'", string)
        return matches
    except Exception as e:
        # In case of an error, print the error and return the original string
        print(f"Error converting string to list: {e}")
        return string


def preprocess(text: str, answers: list) -> str:
    text_after_answer = re.sub(r'^Answer: ', '', text)

    exclude = set(string.punctuation)
    exclude.add("’")
    exclude.add("\n")

    # Remove excluded characters
    cleaned_text = normalize_answer("".join(ch for ch in text_after_answer if ch not in exclude))

    # Replace text with answer item if it matches a substring in the cleaned text
    for answer_item in answers:
        if normalize_answer(answer_item) in cleaned_text:
            return answer_item  # Return the answer item that matches the substring

    return cleaned_text

In [48]:
df['answer'] = df['answer'].apply(string_to_list)
df['predictions'] = df['predictions'].str.replace("^Answer: ", "", regex=True)
df['predictions_em'] = df.apply(lambda row: preprocess(row['predictions'], row['answer']), axis=1)

In [49]:
df.head()

question  \
0      when was the last time anyone was on the moon   
1    who wrote he ain't heavy he's my brother lyrics   
2  how many seasons of the bastard executioner ar...   
3            when did the eagles win last super bowl   
4        who won last year's ncaa women's basketball   

                                  answer  \
0  [14 December 1972 UTC, December 1972]   
1             [Bobby Scott, Bob Russell]   
2                      [one, one season]   
3                                 [2017]   
4                       [South Carolina]   

                                         predictions  \
0  The last time anyone was on the moon was durin...   
1                       Bobby Scott and Bob Russell.   
2  There is only one season of "The Bastard Execu...   
3      The Eagles won their last Super Bowl in 2018.   
4                                  Baylor Lady Bears   

                             predictions_em  
0                             December 1972  
1                               Bobby Scott  
2                                       one  
3  eagles won their last super bowl in 2018  
4                         baylor lady bears

### Calculate Scores

In [50]:
import datasets
from drive.MyDrive.Berkeley.MIDS.DATASCI_266.project.scripts.exact_match import exact_match_score, metric_max_over_ground_truths, f1_score

df['em'] = df.apply(lambda row: metric_max_over_ground_truths(exact_match_score, row['predictions_em'], row['answer']) if row['answer'] and row['predictions_em'] else 0, axis=1)
df['f1'] = df.apply(lambda row: metric_max_over_ground_truths(f1_score, row['predictions_em'], row['answer']) if row['answer'] and row['predictions_em'] else 0, axis=1)

In [51]:
!pip install -q rouge_score
!pip install -q evaluate

In [52]:
import evaluate

df['predictions'] = df['predictions'].astype(str)
df['answer'] = df['answer'].astype(str)

# Filter out rows where either 'predictions' or 'answer' is empty or NaN
filtered_df = df[(df['predictions'].notna() & df['predictions'].str.strip().astype(bool)) &
                 (df['answer'].notna() & df['answer'].str.strip().astype(bool))]
rouge = evaluate.load('rouge')
predictions = filtered_df['predictions'].tolist()
references = filtered_df['answer'].tolist()
rouge_results = rouge.compute(predictions=predictions,
                        references=references)
print(rouge_results)

{'rouge1': 0.21834001257160768, 'rouge2': 0.1116718659853219, 'rougeL': 0.21054033885938062, 'rougeLsum': 0.21131730802805615}


### Prove of correctness

#### Top 10 rows from data frame

In [53]:
df.head(10)

question  \
0      when was the last time anyone was on the moon   
1    who wrote he ain't heavy he's my brother lyrics   
2  how many seasons of the bastard executioner ar...   
3            when did the eagles win last super bowl   
4        who won last year's ncaa women's basketball   
5        when did the isle of wight become an island   
6        love yourself by justin bieber is about who   
7               who was the ruler of england in 1616   
8          what is the hot coffee mod in san andreas   
9  what is the maximum data rate for the 802.11a ...   

                                      answer  \
0  ['14 December 1972 UTC', 'December 1972']   
1             ['Bobby Scott', 'Bob Russell']   
2                      ['one', 'one season']   
3                                   ['2017']   
4                         ['South Carolina']   
5                ['During the last Ice Age']   
6                                ['Rihanna']   
7                                ['James I']   
8      ['a normally inaccessible mini-game']   
9                          ['54\\xa0Mbit/s']   

                                         predictions  \
0  The last time anyone was on the moon was durin...   
1                       Bobby Scott and Bob Russell.   
2  There is only one season of "The Bastard Execu...   
3      The Eagles won their last Super Bowl in 2018.   
4                                  Baylor Lady Bears   
5  The Isle of Wight has been an island for most ...   
6  Justin Bieber's song "Love Yourself" is about ...   
7                King James I of England (1603-1625)   
8  The Hot Coffee mod in San Andreas is a popular...   
9                      54 Mbps (megabits per second)   

                                      predictions_em     em   f1  
0                                      December 1972   True  1.0  
1                                        Bobby Scott   True  1.0  
2                                                one   True  1.0  
3           eagles won their last super bowl in 2018  False  0.0  
4                                  baylor lady bears  False  0.0  
5                            During the last Ice Age   True  1.0  
6  justin biebers song love yourself is about lov...  False  0.0  
7                                            James I   True  1.0  
8  hot coffee mod in san andreas is popular mod t...  False  0.0  
9                        54 mbps megabits per second  False  0.0

#### Top 10 rows from data frame that exactly match one of the reference answer

In [54]:
df_em_true = df[df['em'] == True]
df_em_true.head(10)

question  \
0       when was the last time anyone was on the moon   
1     who wrote he ain't heavy he's my brother lyrics   
2   how many seasons of the bastard executioner ar...   
5         when did the isle of wight become an island   
7                who was the ruler of england in 1616   
10      which state is located in the centre of india   
14        who does the voice of nala in the lion king   
17               who is under the mask of darth vader   
18                 who had a baby at 100 in the bible   
19         what age do you need to be to buy a bb gun   

                                               answer  \
0           ['14 December 1972 UTC', 'December 1972']   
1                      ['Bobby Scott', 'Bob Russell']   
2                               ['one', 'one season']   
5                         ['During the last Ice Age']   
7                                         ['James I']   
10                 ['Chhattisgarh', 'Madhya Pradesh']   
14  ['Niketa Calame', 'Sally Dworsky', 'Moira Kell...   
17                               ['Anakin Skywalker']   
18                               ['Sarah', 'Abraham']   
19                                             ['18']   

                                          predictions  \
0   The last time anyone was on the moon was durin...   
1                        Bobby Scott and Bob Russell.   
2   There is only one season of "The Bastard Execu...   
5   The Isle of Wight has been an island for most ...   
7                 King James I of England (1603-1625)   
10                                     Madhya Pradesh   
14                                        Moira Kelly   
17                                   Anakin Skywalker   
18  Sarah, who had a son named Isaac when she was ...   
19  In most states, you must be at least 18 years ...   

             predictions_em    em   f1  
0             December 1972  True  1.0  
1               Bobby Scott  True  1.0  
2                       one  True  1.0  
5   During the last Ice Age  True  1.0  
7                   James I  True  1.0  
10           Madhya Pradesh  True  1.0  
14              Moira Kelly  True  1.0  
17         Anakin Skywalker  True  1.0  
18                    Sarah  True  1.0  
19                       18  True  1.0

#### Top 10 rows from data frame that doesn't match match any of the reference answer

In [55]:
df_em_true = df[df['em'] == False]
df_em_true.head(10)

question  \
3             when did the eagles win last super bowl   
4         who won last year's ncaa women's basketball   
6         love yourself by justin bieber is about who   
8           what is the hot coffee mod in san andreas   
9   what is the maximum data rate for the 802.11a ...   
11                    who sang i ran all the way home   
12          where did the last name wallace come from   
13  who was the actor that played ben stone on law...   
15       who plays gram on the young and the restless   
16            what is the oath that new citizens take   

                                   answer  \
3                                ['2017']   
4                      ['South Carolina']   
6                             ['Rihanna']   
8   ['a normally inaccessible mini-game']   
9                       ['54\\xa0Mbit/s']   
11                        ['The Impalas']   
12                 ['a Scottish surname']   
13                   ['Michael Moriarty']   
15                        ['Max Shippee']   
16   ['United States Oath of Allegiance']   

                                          predictions  \
3       The Eagles won their last Super Bowl in 2018.   
4                                   Baylor Lady Bears   
6   Justin Bieber's song "Love Yourself" is about ...   
8   The Hot Coffee mod in San Andreas is a popular...   
9                       54 Mbps (megabits per second)   
11                                        The Beatles   
12  The last name "Wallace" originated in Scotland...   
13                                      Sam Waterston   
15                                        Jess Walton   
16                            The Oath of Allegiance.   

                                       predictions_em     em        f1  
3            eagles won their last super bowl in 2018  False  0.000000  
4                                   baylor lady bears  False  0.000000  
6   justin biebers song love yourself is about lov...  False  0.000000  
8   hot coffee mod in san andreas is popular mod t...  False  0.000000  
9                         54 mbps megabits per second  False  0.000000  
11                                            beatles  False  0.000000  
12  last name wallace originated in scotland and i...  False  0.037736  
13                                      sam waterston  False  0.000000  
15                                        jess walton  False  0.000000  
16                                 oath of allegiance  False  0.750000

#### Overall Exact Match & F1 & Rouge scores

In [56]:
overall_em = sum(df['em']) / len(df['em'])
overall_f1 = sum(df['f1']) / len(df['f1'])

# Print the overall Exact Match score, F1 and Rouge score
print(f"Overall Exact Match Score: {overall_em * 100:.2f}")
print(f"Overall F1 Score: {overall_f1 * 100:.2f}")
print(f"Rouge1: {rouge_results['rouge1'] * 100:.2f}")
print(f"Rouge2: {rouge_results['rouge2'] * 100:.2f}")
print(f"RougeL: {rouge_results['rougeL'] * 100:.2f}")
print(f"RougeLSum: {rouge_results['rougeLsum'] * 100:.2f}")

Overall Exact Match Score: 35.96
Overall F1 Score: 40.16
Rouge1: 21.83
Rouge2: 11.17
RougeL: 21.05
RougeLSum: 21.13
